# Build and install the package

First patch `pyo3-polars`:


- Use [this diff](https://github.com/pola-rs/pyo3-polars/compare/main...Magnus167:pyo3-polars:main) to make changes to the `pyo3-polars` package.


Install the package:

```bash
python -m venv .venv

# source .venv/bin/activate
./.venv/Scripts/activate

pip install maturin ipywidgets

maturin develop --release
```


### Import Python packages


In [ ]:
import macrosynergy
import pandas as pd
import numpy as np
import polars as pl
import os

### Import Python bindings - `msyrs`


In [ ]:
import msyrs

In [ ]:
DATA_FOLDER_PATH = "E:/Work/jpmaqs-data"
# DATA_FOLDER_PATH = "C:/Users/PalashTyagi/Code/go-dataquery/jpmaqs-data"
DQ_CLIENT_ID = os.getenv("DQ_CLIENT_ID")
DQ_CLIENT_SECRET = os.getenv("DQ_CLIENT_SECRET")

In [ ]:
dfpath = f"{DATA_FOLDER_PATH}/data/ADPEMPL_SA_P1M1ML1/USD_ADPEMPL_SA_P1M1ML1.csv"


ldf: pl.DataFrame = msyrs.qdf.load_qdf(dfpath)
ldf.head(5)

In [ ]:
cids_dm = "AUD.CAD.CHF.EUR.GBP.JPY.NOK.NZD.SEK.USD".split(".")
cids_em = "CLP.COP.CZK.HUF.IDR.ILS.INR.KRW.MXN.PLN.THB.TRY.TWD.ZAR".split(".")
cids = cids_dm + cids_em
cids_dux = list(set(cids) - set(["IDR", "NZD"]))
ecos = "CPIC_SA_P1M1ML12.CPIC_SJA_P3M3ML3AR.CPIC_SJA_P6M6ML6AR.CPIH_SA_P1M1ML12.CPIH_SJA_P3M3ML3AR.CPIH_SJA_P6M6ML6AR.INFTEFF_NSA.INTRGDP_NSA_P1M1ML12_3MMA.INTRGDPv5Y_NSA_P1M1ML12_3MMA.PCREDITGDP_SJA_D1M1ML12.RGDP_SA_P1Q1QL4_20QMA.RYLDIRS02Y_NSA.RYLDIRS05Y_NSA.PCREDITBN_SJA_P1M1ML12".split(
    "."
)


mkts = "DU02YXR_NSA.DU05YXR_NSA.DU02YXR_VT10.DU05YXR_VT10.EQXR_NSA.EQXR_VT10.FXXR_NSA.FXXR_VT10.FXCRR_NSA.FXTARGETED_NSA.FXUNTRADABLE_NSA".split(
    "."
)
xcats = ecos + mkts

tickers = [f"{c}_{x}" for c in cids for x in xcats]

In [ ]:
downloaded_df: pl.DataFrame = msyrs.download.download_jpmaqs_indicators_as_df(
    client_id=DQ_CLIENT_ID,
    client_secret=DQ_CLIENT_SECRET,
    tickers=tickers,
)
downloaded_df.head(5)

In [ ]:
big_df: pl.DataFrame = msyrs.qdf.load_qdf_from_download_bank(
    folder_path=DATA_FOLDER_PATH, tickers=tickers
)
big_df.head(5)

In [ ]:
big_df.estimated_size("mb")

In [ ]:
big_df.to_pandas().memory_usage(deep=True).sum() / 1024**2

In [ ]:
macrosynergy.management.types.QuantamentalDataFrame(big_df.to_pandas()).memory_usage(
    deep=True
).sum() / 1024**2

In [ ]:
sel_cids = ["USD", "EUR", "GBP", "AUD", "CAD"]
start = "2024-11-14"

In [ ]:
eq_df = msyrs.qdf.reduce_dataframe(
    df=big_df,
    cids=sel_cids,
    xcats=["EQXR_NSA", "EQXR_VT10"],
    start=start,
)
eq_df

In [ ]:
fx_xcats = [xc for xc in xcats if xc.startswith("FX")]
fx_df = msyrs.qdf.reduce_dataframe(
    df=big_df, cids=sel_cids, start=start, xcats=fx_xcats, intersect=True
)

In [ ]:
new_df: pl.DataFrame = msyrs.qdf.update_dataframe(df=eq_df, df_add=fx_df)

new_df.head(10)

In [ ]:
new_df.tail(10)